# EDA - Day-ahead electricity prices (France)

### Bibliothèques

In [33]:
import urllib.request
import os
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.figure_factory as ff
from statsmodels.tsa.seasonal import STL
import seaborn as sns
import skimpy as sk
import summarytools as st
from datetime import datetime
import warnings
warnings.filterwarnings('ignore')
import plotly.io as pio
import calendar
pio.templates.default = "plotly_white"

print("Environnement configuré avec succès!")
print(f"Date d'exécution: {datetime.now().strftime('%Y-%m-%d %H:%M')}")


Environnement configuré avec succès!
Date d'exécution: 2025-11-26 10:38


### Dataset

In [2]:
# Créer dossier data si inexistant
os.makedirs('../data/raw', exist_ok=True)

# URL dataset 60min
url = "https://data.open-power-system-data.org/time_series/latest/time_series_60min_singleindex.csv"
destination = "../data/raw/time_series_60min.csv"

# Télécharger si pas déjà présent
if not os.path.exists(destination):
    print("⏳ Téléchargement du dataset (124 MB)... Patience!")
    urllib.request.urlretrieve(url, destination)
    print("Dataset téléchargé!")
else:
    print(" Dataset déjà présent localement")


 Dataset déjà présent localement


## Traitement et préparation des données

In [3]:
# Charger dataset
df = pd.read_csv('../data/raw/time_series_60min.csv',
    parse_dates=['utc_timestamp', 'cet_cest_timestamp'],
    low_memory=False
)

In [4]:
# Définir timestamp comme index
df = df.set_index('utc_timestamp')

print(f" Shape du dataset: {df.shape}")
print(f" Période: {df.index.min()} → {df.index.max()}")
print(f"\n Premières lignes:")
df.head(5)

 Shape du dataset: (50401, 299)
 Période: 2014-12-31 23:00:00+00:00 → 2020-09-30 23:00:00+00:00

 Premières lignes:


cet_cest_timestamp  \
utc_timestamp                                          
2014-12-31 23:00:00+00:00  2015-01-01 00:00:00+01:00   
2015-01-01 00:00:00+00:00  2015-01-01 01:00:00+01:00   
2015-01-01 01:00:00+00:00  2015-01-01 02:00:00+01:00   
2015-01-01 02:00:00+00:00  2015-01-01 03:00:00+01:00   
2015-01-01 03:00:00+00:00  2015-01-01 04:00:00+01:00   

                           AT_load_actual_entsoe_transparency  \
utc_timestamp                                                   
2014-12-31 23:00:00+00:00                                 NaN   
2015-01-01 00:00:00+00:00                              5946.0   
2015-01-01 01:00:00+00:00                              5726.0   
2015-01-01 02:00:00+00:00                              5347.0   
2015-01-01 03:00:00+00:00                              5249.0   

                           AT_load_forecast_entsoe_transparency  \
utc_timestamp                                                     
2014-12-31 23:00:00+00:00                                   NaN   
2015-01-01 00:00:00+00:00                                6701.0   
2015-01-01 01:00:00+00:00                                6593.0   
2015-01-01 02:00:00+00:00                                6482.0   
2015-01-01 03:00:00+00:00                                6454.0   

                           AT_price_day_ahead  AT_solar_generation_actual  \
utc_timestamp                                                               
2014-12-31 23:00:00+00:00                 NaN                         NaN   
2015-01-01 00:00:00+00:00                35.0                         NaN   
2015-01-01 01:00:00+00:00                45.0                         NaN   
2015-01-01 02:00:00+00:00                41.0                         NaN   
2015-01-01 03:00:00+00:00                38.0                         NaN   

                           AT_wind_onshore_generation_actual  \
utc_timestamp                                                  
2014-12-31 23:00:00+00:00                                NaN   
2015-01-01 00:00:00+00:00                               69.0   
2015-01-01 01:00:00+00:00                               64.0   
2015-01-01 02:00:00+00:00                               65.0   
2015-01-01 03:00:00+00:00                               64.0   

                           BE_load_actual_entsoe_transparency  \
utc_timestamp                                                   
2014-12-31 23:00:00+00:00                                 NaN   
2015-01-01 00:00:00+00:00                              9484.0   
2015-01-01 01:00:00+00:00                              9152.0   
2015-01-01 02:00:00+00:00                              8799.0   
2015-01-01 03:00:00+00:00                              8567.0   

                           BE_load_forecast_entsoe_transparency  \
utc_timestamp                                                     
2014-12-31 23:00:00+00:00                                   NaN   
2015-01-01 00:00:00+00:00                                9897.0   
2015-01-01 01:00:00+00:00                                9521.0   
2015-01-01 02:00:00+00:00                                9135.0   
2015-01-01 03:00:00+00:00                                8909.0   

                           BE_solar_generation_actual  \
utc_timestamp                                           
2014-12-31 23:00:00+00:00                         NaN   
2015-01-01 00:00:00+00:00                         NaN   
2015-01-01 01:00:00+00:00                         NaN   
2015-01-01 02:00:00+00:00                         NaN   
2015-01-01 03:00:00+00:00                         NaN   

                           BE_wind_generation_actual  ...  \
utc_timestamp                                         ...   
2014-12-31 23:00:00+00:00                        NaN  ...   
2015-01-01 00:00:00+00:00                        NaN  ...   
2015-01-01 01:00:00+00:00                     734.81  ...   
2015-01-01 02:00:00+00:00                     766.64  ...   
2015-01-01 03:00:00+00:00         

**Focus sur la FRANCE**

In [5]:
# Sélection des colonnes françaises
france_cols = [col for col in df.columns if 'FR' in col]
df_france = df[france_cols].copy()

# Résumé du dataset France
print("\nRésumé du dataset France:")
print(f"Dimensions: {df_france.shape[0]} lignes × {df_france.shape[1]} colonnes")
print(f"Période: {df_france.index.min()} à {df_france.index.max()}")
# Aperçu des premières lignes
print("\n📊 Aperçu des données:")
df_france.head()


Résumé du dataset France:
Dimensions: 50401 lignes × 5 colonnes
Période: 2014-12-31 23:00:00+00:00 à 2020-09-30 23:00:00+00:00

📊 Aperçu des données:


FR_load_actual_entsoe_transparency  \
utc_timestamp                                                   
2014-12-31 23:00:00+00:00                                 NaN   
2015-01-01 00:00:00+00:00                                 NaN   
2015-01-01 01:00:00+00:00                             69773.0   
2015-01-01 02:00:00+00:00                             66417.0   
2015-01-01 03:00:00+00:00                             64182.0   

                           FR_load_forecast_entsoe_transparency  \
utc_timestamp                                                     
2014-12-31 23:00:00+00:00                                   NaN   
2015-01-01 00:00:00+00:00                                   NaN   
2015-01-01 01:00:00+00:00                               69750.0   
2015-01-01 02:00:00+00:00                               66300.0   
2015-01-01 03:00:00+00:00                               63250.0   

                           FR_solar_generation_actual  \
utc_timestamp                                           
2014-12-31 23:00:00+00:00                         NaN   
2015-01-01 00:00:00+00:00                         NaN   
2015-01-01 01:00:00+00:00                         NaN   
2015-01-01 02:00:00+00:00                         NaN   
2015-01-01 03:00:00+00:00                         NaN   

                           FR_wind_onshore_generation_actual  \
utc_timestamp                                                  
2014-12-31 23:00:00+00:00                                NaN   
2015-01-01 00:00:00+00:00                                NaN   
2015-01-01 01:00:00+00:00                             1464.0   
2015-01-01 02:00:00+00:00                             1543.0   
2015-01-01 03:00:00+00:00                             1579.0   

                           IT_NORD_FR_price_day_ahead  
utc_timestamp                                          
2014-12-31 23:00:00+00:00                         NaN  
2015-01-01 00:00:00+00:00                         NaN  
2015-01-01 01:00:00+00:00                         NaN  
2015-01-01 02:00:00+00:00                         NaN  
2015-01-01 03:00:00+00:00                         NaN

***Stats Descriptives***

In [6]:
df_france.describe()

FR_load_actual_entsoe_transparency  \
count                        50357.000000   
mean                         53249.737792   
std                          11684.346489   
min                          29398.000000   
25%                          44314.000000   
50%                          51536.000000   
75%                          61246.000000   
max                         158000.000000   

       FR_load_forecast_entsoe_transparency  FR_solar_generation_actual  \
count                          50398.000000                50386.000000   
mean                           53337.475971                 1109.213551   
std                            11829.079271                 1557.134702   
min                            29050.000000                    0.000000   
25%                            44250.000000                    0.000000   
50%                            51600.000000                  153.000000   
75%                            61500.000000                 1966.000000   
max                            95150.000000                 7417.000000   

       FR_wind_onshore_generation_actual  IT_NORD_FR_price_day_ahead  
count                       50393.000000                25576.000000  
mean                         2945.102971                   49.599747  
std                          2275.338361                   16.571235  
min                           262.000000                    5.000000  
25%                          1315.000000                   39.047500  
50%                          2187.000000                   47.470000  
75%                          3863.000000                   56.300000  
max                         12976.000000                  206.120000

In [7]:
sk.skim(df_france)

╭──────────────────────────────────────────────── skimpy summary ─────────────────────────────────────────────────╮
│          Data Summary                Data Types                                                                 │
│ ┏━━━━━━━━━━━━━━━━━━━┳━━━━━━━━┓ ┏━━━━━━━━━━━━━┳━━━━━━━┓                                                          │
│ ┃ Dataframe         ┃ Values ┃ ┃ Column Type ┃ Count ┃                                                          │
│ ┡━━━━━━━━━━━━━━━━━━━╇━━━━━━━━┩ ┡━━━━━━━━━━━━━╇━━━━━━━┩                                                          │
│ │ Number of rows    │ 50401  │ │ float64     │ 5     │                                                          │
│ │ Number of columns │ 5      │ └─────────────┴───────┘                                                          │
│ └───────────────────┴────────┘                                                                                  │
│                                                     number                                                      │
│ ┏━━━━━━━━━━━━━━━━┳━━━━━━━┳━━━━━━━━━━━━━━━━━┳━━━━━━━┳━━━━━━━┳━━━━━━━┳━━━━━━━┳━━━━━━━┳━━━━━━━┳━━━━━━━━┳━━━━━━━━┓  │
│ ┃ column         ┃ NA    ┃ NA %            ┃ mean  ┃ sd    ┃ p0    ┃ p25   ┃ p50   ┃ p75   ┃ p100   ┃ hist   ┃  │
│ ┡━━━━━━━━━━━━━━━━╇━━━━━━━╇━━━━━━━━━━━━━━━━━╇━━━━━━━╇━━━━━━━╇━━━━━━━╇━━━━━━━╇━━━━━━━╇━━━━━━━╇━━━━━━━━╇━━━━━━━━┩  │
│ │ FR_load_actual │    44 │ 0.0872998551616 │ 53250 │ 11680 │ 29400 │ 44310 │ 51540 │ 61250 │ 158000 │  ▇▇▁   │  │
│ │ _entsoe_transp │       │            0393 │       │       │       │       │       │       │        │        │  │
│ │ arency         │       │                 │       │       │       │       │       │       │        │        │  │
│ │ FR_load_foreca │     3 │ 0.0059522628519 │ 53340 │ 11830 │ 29050 │ 44250 │ 51600 │ 61500 │  95150 │ ▃▇▆▃▁  │  │
│ │ st_entsoe_tran │       │           27541 │       │       │       │       │       │       │        │        │  │
│ │ sparency       │       │                 │       │       │       │       │       │       │        │        │  │
│ │ FR_solar_gener │    15 │ 0.0297613142596 │  1109 │  1557 │     0 │     0 │   153 │  1966 │   7417 │  ▇▂▁▁  │  │
│ │ ation_actual   │       │           37704 │       │       │       │       │       │       │        │        │  │
│ │ FR_wind_onshor │     8 │ 0.0158727009384 │  2945 │  2275 │   262 │  1315 │  2187 │  3863 │  12980 │  ▇▃▂▁  │  │
│ │ e_generation_a │       │            7344 │       │       │       │       │       │       │        │        │  │
│ │ ctual          │       │                 │       │       │       │       │       │       │        │        │  │
│ │ IT_NORD_FR_pri │ 24825 │ 49.254975099700 │  49.6 │ 16.57 │     5 │ 39.05 │ 47.47 │  56.3 │  206.1 │  ▃▇▁   │  │
│ │ ce_day_ahead   │       │               4 │       │       │       │       │       │       │        │        │  │
│ └────────────────┴───────┴─────────────────┴───────┴───────┴───────┴───────┴───────┴───────┴────────┴────────┘  │
╰────────────────────────────────────────────────────── End ──────────────────────────────────────────────────────╯

In [8]:
st.dfSummary(df_france)

***Valeurs manquantes et doublons***

* Doublons

In [9]:
# Vérification des doublons sur l'index utc_timestamp
total = len(df_france)
unique = df_france.index.nunique()
dup = total - unique

print(f"Total lignes: {total}")
print(f"Lignes uniques par utc_timestamp: {unique}")
print(f"Doublons détectés: {dup}")

if dup:
    dup_timestamps = df.index[df.index.duplicated(keep=False)].unique()
    print(f"Nombre de timestamps dupliqués uniques: {len(dup_timestamps)}")
    display(pd.DataFrame({"duplicated_timestamp": dup_timestamps}).head(20))
    # Afficher un échantillon des lignes dupliquées pour inspection
    sample_ts = dup_timestamps[:5]
    for ts in sample_ts:
        print(f"\nExemple pour timestamp dupliqué: {ts}")
        display(df_france.loc[ts])
else:
    print("Aucun doublon trouvé sur utc_timestamp.")

Total lignes: 50401
Lignes uniques par utc_timestamp: 50401
Doublons détectés: 0
Aucun doublon trouvé sur utc_timestamp.


* Valeurs manquantes

In [10]:
# Quantification et visualisation des valeurs manquantes (df_france)

missing_count = df_france.isna().sum()
missing_pct = (missing_count / len(df_france)) * 100
missing_df_all = (
    pd.DataFrame({"missing_count": missing_count, "missing_pct": missing_pct})
    .sort_values("missing_pct", ascending=False)
)
display(missing_df_all)

# Bar plot des pourcentages de valeurs manquantes
fig_missing_bar = px.bar(
    missing_df_all.reset_index().rename(columns={"index": "column"}),
    x="missing_pct",
    y="column",
    orientation="h",
    text="missing_pct",
    title="Pourcentage de valeurs manquantes par colonne (df_france)",
    labels={"missing_pct": "% NaN", "column": "Colonne"},
)
fig_missing_bar.update_traces(texttemplate="%{text:.2f}%", textposition="outside")

fig_missing_bar.show()

missing_count  missing_pct
IT_NORD_FR_price_day_ahead                    24825    49.254975
FR_load_actual_entsoe_transparency               44     0.087300
FR_solar_generation_actual                       15     0.029761
FR_wind_onshore_generation_actual                 8     0.015873
FR_load_forecast_entsoe_transparency              3     0.005952

In [12]:
# Périodes avec valeurs manquantes pour IT_NORD_FR_price_day_ahead
col = "IT_NORD_FR_price_day_ahead"
mask = df_france[col].isna()

if not mask.any():
    print(f"Aucune valeur manquante pour {col}.")
else:
    # numéroter les runs (changes de state)
    run_id = (mask != mask.shift(1)).cumsum()
    runs = (
        df_france[mask]
        .groupby(run_id[mask])
        .apply(lambda x: pd.Series({
            "start": x.index.min(),
            "end": x.index.max(),
            "n_points": len(x)
        }))
        .reset_index(drop=True)
    )
    runs["duration_hours"] = (runs["end"] - runs["start"]) / np.timedelta64(1, "h") + 1
    runs = runs.sort_values("start").reset_index(drop=True)

    print(f"Nombre de périodes disjointes avec des NaN pour {col} : {len(runs)}")
    display(runs)

    overall = pd.Series({
        "first_nan": runs["start"].min(),
        "last_nan": runs["end"].max(),
        "total_nan_points": int(mask.sum()),
        "total_points": len(df_france),
        "nan_pct": mask.mean() * 100
    })
    display(overall)

Nombre de périodes disjointes avec des NaN pour IT_NORD_FR_price_day_ahead : 5


start                       end  n_points  \
0 2014-12-31 23:00:00+00:00 2015-01-04 23:00:00+00:00        97   
1 2015-03-29 02:00:00+00:00 2015-03-29 03:00:00+00:00         2   
2 2016-03-27 02:00:00+00:00 2016-03-27 03:00:00+00:00         2   
3 2017-03-26 02:00:00+00:00 2017-03-26 03:00:00+00:00         2   
4 2017-12-05 22:00:00+00:00 2020-09-30 23:00:00+00:00     24722   

   duration_hours  
0            97.0  
1             2.0  
2             2.0  
3             2.0  
4         24722.0

first_nan           2014-12-31 23:00:00+00:00
last_nan            2020-09-30 23:00:00+00:00
total_nan_points                        24825
total_points                            50401
nan_pct                             49.254975
dtype: object

***Renommage des colonne pour plus de clartée***

In [13]:
df_france.rename(columns={
            'IT_NORD_FR_price_day_ahead': 'price',
            'FR_load_actual_entsoe_transparency': 'load_actual',
            'FR_load_forecast_entsoe_transparency': 'load_forecast',
            'FR_solar_generation_actual': 'solar_generation',
            'FR_wind_onshore_generation_actual': 'wind_generation'
        }, inplace=True)

***Troncature des données ---***
***Limite du DataFrame à la plage de dates pour laquelle les données de prix sont disponibles***

In [14]:
start_date = '2015-01-05'
end_date = '2017-12-05'
df_france = df_france.loc[start_date:end_date]

In [15]:
missing_count = df_france.isna().sum()
missing_pct = (missing_count / len(df_france)) * 100
missing_df_all = (
    pd.DataFrame({"missing_count": missing_count, "missing_pct": missing_pct})
    .sort_values("missing_pct", ascending=False)
)
display(missing_df_all)

missing_count  missing_pct
load_actual                  13     0.050813
price                         8     0.031270
load_forecast                 0     0.000000
solar_generation              0     0.000000
wind_generation               0     0.000000

***--- Imputation des valeurs manquantes ---***

In [16]:
# Utiliser l'interpolation linéaire pour les quelques NaN restants
df_france.interpolate(method='linear', inplace=True)

In [17]:
missing_count = df_france.isna().sum()
missing_pct = (missing_count / len(df_france)) * 100
missing_df_all = (
    pd.DataFrame({"missing_count": missing_count, "missing_pct": missing_pct})
    .sort_values("missing_pct", ascending=False)
)
display(missing_df_all)

missing_count  missing_pct
load_actual                   0          0.0
load_forecast                 0          0.0
solar_generation              0          0.0
wind_generation               0          0.0
price                         0          0.0

In [19]:
df_france.head()

load_actual  load_forecast  solar_generation  \
utc_timestamp                                                             
2015-01-05 00:00:00+00:00      61092.0        60250.0               0.0   
2015-01-05 01:00:00+00:00      60219.0        59650.0               0.0   
2015-01-05 02:00:00+00:00      57535.0        56500.0               0.0   
2015-01-05 03:00:00+00:00      56891.0        55050.0               0.0   
2015-01-05 04:00:00+00:00      59823.0        56750.0               0.0   

                           wind_generation  price  
utc_timestamp                                      
2015-01-05 00:00:00+00:00           1048.0  39.10  
2015-01-05 01:00:00+00:00           1010.0  35.21  
2015-01-05 02:00:00+00:00            947.0  32.43  
2015-01-05 03:00:00+00:00            821.0  33.15  
2015-01-05 04:00:00+00:00            760.0  38.85

## Analyse exploratoire

* ***Analyse du "Price"***

In [22]:
# Distribution du prix day-ahead en France
fig = px.histogram(
    df_france,
    x="price",
    nbins=25,
    marginal="rug",           
    opacity=0.75,
    title="Distribution du Day-Ahead Price (€/MWh)",
    labels={"price": "Price (€/MWh)", "count": "Frequency"},
)

fig.update_layout(
    bargap=0.02,
    template="plotly_white",
)

fig.show()                  

In [ ]:
fig = px.line(
    df_france.reset_index(),
    x=df_france.index.name or "index",
    y="price",
    title="Evolution du Day-Ahead Price (2015-2017)",
    labels={
        df_france.index.name or "index": "Date",
        "price": "Price (€/MWh)",
    },
)
fig.update_layout(template="plotly_white")
fig.show()                             

* ***Saisonnalité***

In [47]:
#Analyse de la saisonnalité
df_seasonal = df_france.copy()
df_seasonal['month'] = df_seasonal.index.month_name()
df_seasonal['day_of_week'] = df_seasonal.index.day_name()
df_seasonal['hour'] = df_seasonal.index.hour

In [48]:
# Saisonnalité annuelle : distribution mensuelle des prix

fig = px.box(
    df_seasonal,
    x="month",
    y="price",
    points="outliers", 
    title="Saisonnalité annuelle : distribution mensuelle des prix",
    labels={"month": "Mois", "price": "Prix (€/MWh)"},
    template="plotly_white",
)
fig.update_layout(xaxis=dict(dtick=1))

fig.show()

In [28]:
# Saisonnalité hebdomadaire : distribution des prix par jour de la semaine

day_order = ["Monday", "Tuesday", "Wednesday", "Thursday", "Friday", "Saturday", "Sunday"]

fig = px.box(
    df_seasonal,
    x="day_of_week",
    y="price",
    category_orders={"day_of_week": day_order},
    points="outliers",
    title="Saisonnalité hebdomadaire : distribution des prix par jour de la semaine",
    labels={"day_of_week": "Jour de la semaine", "price": "Prix (€/MWh)"},
    template="plotly_white",
)
fig.update_xaxes(tickangle=-45)

fig.show()

In [29]:
# Saisonnalité quotidienne : distribution des prix par heure

fig = px.box(
    df_seasonal,
    x="hour",
    y="price",
    points="outliers",
    title="Saisonnalité quotidienne : distribution des prix par heure",
    labels={"hour": "Heure de la journée", "price": "Prix (€/MWh)"},
    template="plotly_white",
)
fig.update_xaxes(dtick=1)

fig.show()

In [41]:
# Semaine vs week-end
df_seasonal["week_period"] = np.where(
    df_seasonal["day_of_week"].isin(["Saturday", "Sunday"]),
    "Weekend",
    "Weekday",
)

fig_week = px.box(
    df_seasonal,
    x="week_period",
    y="price",
    color="week_period",
    points="outliers",
    title="Distribution des prix : Semaine vs Week-end",
    labels={"week_period": "", "price": "Prix (€/MWh)"},
    template="plotly_white",
)
fig_week.update_layout(showlegend=False)
fig_week.show()

In [49]:
# Saisons (été/hiver/printemps/automne)
SEASON_LABELS = {
    "December": "Winter", "January": "Winter", "February": "Winter",
    "March": "Spring", "April": "Spring", "May": "Spring",
    "June": "Summer", "July": "Summer", "August": "Summer",
    "September": "Autumn", "October": "Autumn", "November": "Autumn",
}
df_seasonal["season"] = df_seasonal["month"].map(SEASON_LABELS)
season_order = ["Winter", "Spring", "Summer", "Autumn"]

fig_season = px.box(
    df_seasonal,
    x="season",
    y="price",
    category_orders={"season": season_order},
    points="outliers",
    title="Distribution des prix : Saisons",
    labels={"season": "Saison", "price": "Prix (€/MWh)"},
    template="plotly_white",
)
fig_season.show()

***Stats***

In [32]:
print("\n--- Statistique des prix ---")
print(df_france['price'].describe())


--- Statistique des prix ---
count    25584.000000
mean        49.598433
std         16.572600
min          5.000000
25%         39.030000
50%         47.460000
75%         56.300000
max        206.120000
Name: price, dtype: float64


## Analyse des correlations

* ***Calcul de la matrice de corrélation***

In [52]:
# Matrice de correlation 
corr_matrix = df_france.corr(method='pearson')

In [53]:
# Heatmap de la matrice de corrélation

fig = px.imshow(
    corr_matrix,
    text_auto=".2f",
    color_continuous_scale="RdBu",
    zmin=-1,
    zmax=1,
    title="Correlation Matrix of Variables",
    labels=dict(x="Variables", y="Variables", color="Corr"),
)
fig.update_layout(height=800, width=900, template="plotly_white")

fig.show() 